#Predicting sentiment from product reviews

#Fire up GraphLab Create

In [1]:
import graphlab

#Read some product review data

Loading reviews for a set of baby products. 

In [2]:
products = graphlab.SFrame('amazon_baby.gl/')

[INFO] graphlab.cython.cy_server: GraphLab Create v2.1 started. Logging: /tmp/graphlab_server_1481134247.log
INFO:graphlab.cython.cy_server:GraphLab Create v2.1 started. Logging: /tmp/graphlab_server_1481134247.log


This non-commercial license of GraphLab Create for academic use is assigned to sangeet.saurabh@gmail.com and will expire on December 02, 2017.


#Let's explore this data together

Data includes the product name, the review text and the rating of the review. 

In [18]:
graphlab.canvas.set_target('ipynb')
products.show()

In [3]:
products.head()

Columns:
	name	str
	review	str
	rating	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
[10 rows x 3 columns]

#Build the word count vector for each review

In [20]:
d = {'X' : [0,1,2,3,4], 'Y' : ["I am a cat","what a shot!","dunk it!","Best basketball ever","awesome shot by a batsman"]}
test = graphlab.SFrame(d)

test['word_count'] = graphlab.text_analytics.count_words(test['Y'])
test.head()

Columns:
	X	int
	Y	str
	word_count	dict

Rows: 5

Data:
+---+---------------------------+-------------------------------+
| X |             Y             |           word_count          |
+---+---------------------------+-------------------------------+
| 0 |         I am a cat        | {'a': 1, 'i': 1, 'am': 1, ... |
| 1 |        what a shot!       | {'a': 1, 'what': 1, 'shot!... |
| 2 |          dunk it!         |     {'dunk': 1, 'it!': 1}     |
| 3 |    Best basketball ever   | {'basketball': 1, 'ever': ... |
| 4 | awesome shot by a batsman | {'a': 1, 'awesome': 1, 'ba... |
+---+---------------------------+-------------------------------+
[5 rows x 3 columns]

In [4]:
products['word_count'] = graphlab.text_analytics.count_words(products['review'])

In [5]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+
|           word_count          |
+-------------------------------+
| {'and': 5, '6': 1, 'stink'... |
| {'and': 3, 'love': 1, 'it'... |
| {'and': 2, 'quilt': 1, 'it... |
| {'ingenious': 1, 'and': 3,... |
| {'and': 2, 'parents!!': 1,... |
| {'and': 2, 'this': 2, 'her... |
| {'shop': 1, 'noble': 1, 'i... |
| {'and': 2, 'all': 1, 'righ... |
| {'and': 1, 'help': 1, 'giv... |
| {'journal.': 1, 'nanny': 1... |
+-------------------------------+
[10 rows x 4 columns]

In [6]:
graphlab.canvas.set_target('ipynb')

In [7]:
products['name'].show()

#Examining the reviews for most-sold product:  'Vulli Sophie the Giraffe Teether'

In [21]:
giraffe_reviews = products[products['name'] == 'Vulli Sophie the Giraffe Teether']

In [22]:
len(giraffe_reviews)

723

In [25]:
giraffe_reviews['rating'].show(view='Categorical')

#Build a sentiment classifier

In [26]:
products['rating'].show(view='Categorical')

##Define what's a positive and a negative sentiment

We will ignore all reviews with rating = 3, since they tend to have a neutral sentiment.  Reviews with a rating of 4 or higher will be considered positive, while the ones with rating of 2 or lower will have a negative sentiment.   

In [27]:
#ignore all 3* reviews
products = products[products['rating'] != 3]

In [36]:
#positive sentiment = 4* or 5* reviews
products['sentiment'] = products['rating'] >=4

In [37]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+
|           word_count          | sentiment |
+-------------------------------+-----------+
| {'and': 3, 'love': 1, 'it'... |     1     |
| {'and': 2, 'quilt': 1, 'it... |     1     |
| {'ingenious': 1, 'and': 3,... |     1     |
| {'and': 2, 'parents!!': 1,... |     1     |
| {'and': 2, 'this': 2, 'her... |     1     |
| {'shop': 1, 'noble': 1, 'i... |     1     |
| {'and': 2, 'all': 1, 'righ... |     1     |
| {'and': 1, 'help': 1, 'giv... |     1     |
| {'journal.': 1, 'nanny': 1... |     1     |
| {'all': 1, 'forget': 1, 'j... |     1     |
+-------------------------------+-----------+
[10 rows x 5 columns]

##Let's train the sentiment classifier

In [33]:
train_data,test_data = products.random_split(.8, seed=0)

In [35]:
sentiment_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                                     features=['word_count'],
                                                     validation_set=test_data)

WARNING: The number of feature dimensions in this problem is very large in comparison with the number of examples. Unless an appropriate regularization value is set, this model may not provide accurate predictions for a validation/test set.

Logistic regression:

--------------------------------------------------------

Number of examples          : 133448

Number of classes           : 2

...

| 9         | 17       | 1.000000  | 16.645200    | 0.987066          | 0.919709            |

| 10        | 18       | 1.000000  | 17.927645    | 0.988715          | 0.916256            |

+-----------+----------+-----------+--------------+-------------------+---------------------+

TERMINATED: Iteration limit reached.

This model may not be optimal. To improve it, consider increasing `max_iterations`.

#Evaluate the sentiment model

In [38]:
sentiment_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 100001
 
 Data:
 +-----------+----------------+----------------+-------+------+
 | threshold |      fpr       |      tpr       |   p   |  n   |
 +-----------+----------------+----------------+-------+------+
 |    0.0    |      1.0       |      1.0       | 27976 | 5328 |
 |   1e-05   | 0.909346846847 | 0.998856162425 | 27976 | 5328 |
 |   2e-05   | 0.896021021021 | 0.998748927652 | 27976 | 5328 |
 |   3e-05   | 0.886448948949 | 0.998462968259 | 27976 | 5328 |
 |   4e-05   | 0.879692192192 | 0.998284243637 | 27976 | 5328 |
 |   5e-05   | 0.875187687688 | 0.998212753789 | 27976 | 5328 |
 |   6e-05   | 0.872184684685 | 0.998177008865 | 27976 | 5328 |
 |   7e-05   | 0.868618618619 | 0.998034029168 | 27976 | 5328 |
 |   8e-05   | 0.864677177177 | 0.997998284244 | 27976 | 5328 |
 |   9e-05   | 0.860735735736 | 0.997962539319 | 27976 | 5328 |
 +-----------+----------------+----------------+-------+------

In [39]:
sentiment_model.show(view='Evaluation')

#Applying the learned model to understand sentiment for Giraffe

In [40]:
giraffe_reviews['predicted_sentiment'] = sentiment_model.predict(giraffe_reviews, output_type='probability')

In [41]:
giraffe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | He likes chewing on all th... |  5.0   |
| Vulli Sophie the Giraffe T... | My son loves this toy and ... |  5.0   |
| Vulli Sophie the Giraffe T... | There really should be a l... |  1.0   |
| Vulli Sophie the Giraffe T... | All the moms in my moms' g... |  5.0   |
| Vulli Sophie the Giraffe T... | I was a little skeptical o... |  5.0   |
| Vulli Sophie the Giraffe T... | I have been reading about ... |  5.0   |
| Vulli Sophie the Giraffe T... | My neice loves her sophie ... |  5.0   |
| Vulli Sophie the Giraffe T... | What a friendly face!  And... |  5.0   |
| Vulli Sophie the Giraffe T... | We got this just for my so... |  5.0   |
| Vulli Sophie the Giraffe T... | This product is without a ... |  5.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+---------------------+
|           word_count          | sentiment | predicted_sentiment |
+-------------------------------+-----------+---------------------+
| {'and': 1, 'all': 1, 'beca... |     1     |    0.999513023521   |
| {'and': 1, 'right': 1, 'he... |     1     |    0.999320678306   |
| {'and': 2, 'all': 1, 'woul... |     0     |    0.013558811687   |
| {'and': 2, 'one!': 1, 'all... |     1     |    0.995769474148   |
| {'and': 3, 'all': 1, 'mont... |     1     |    0.662374415673   |
| {'and': 6, 'seven': 1, 'al... |     1     |    0.999997148186   |
| {'and': 4, 'drooling,': 1,... |     1     |    0.989190989536   |
| {'and': 3, 'chew': 1, 'be'... |     1     |    0.999563518413   |
| {'chew': 2, 'seemed': 1, '... |     1     |    0.970160542725   |
| {'and': 4, ':)': 1, 'just'... |     1     |    0.999999795012   |
+-------------------------------+-----------+---------------------+
[10 rows x 6 columns]

##Sort the reviews based on the predicted sentiment and explore

In [42]:
giraffe_reviews = giraffe_reviews.sort('predicted_sentiment', ascending=False)

In [44]:
giraffe_reviews.tail()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | I bought it for my 8 month... |  2.0   |
| Vulli Sophie the Giraffe T... | When we first got it I tho... |  2.0   |
| Vulli Sophie the Giraffe T... | After getting this for my ... |  1.0   |
| Vulli Sophie the Giraffe T... | My daughter loves Sophie, ... |  2.0   |
| Vulli Sophie the Giraffe T... | "Sophie the Giraffe" has t... |  1.0   |
| Vulli Sophie the Giraffe T... | I received this in a box s... |  2.0   |
| Vulli Sophie the Giraffe T... | I was intrigued with the i... |  2.0   |
| Vulli Sophie the Giraffe T... | I wanted to love this prod... |  1.0   |
| Vulli Sophie the Giraffe T... | This children's toy is nos... |  1.0   |
| Vulli Sophie the Giraffe T... | My son (now 2.5) LOVED his... |  1.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+---------------------+
|           word_count          | sentiment | predicted_sentiment |
+-------------------------------+-----------+---------------------+
| {'and': 5, 'enjoy': 1, 'ri... |     0     |  8.31949388805e-07  |
| {'and': 2, 'cute': 1, 'all... |     0     |  5.00559975211e-07  |
| {'just': 1, 'being': 1, 'o... |     0     |  2.65117165834e-07  |
| {'and': 2, 'the': 3, "don'... |     0     |  2.16499014337e-07  |
| {'saying': 1, 'nitrosamine... |     0     |  1.49651158012e-07  |
| {'cute': 1, 'unhooked': 1,... |     0     |  1.30304527009e-07  |
| {'baby.)': 1, 'all': 2, 'a... |     0     |  1.01396472897e-07  |
| {'just': 1, 'may,': 1, 'ch... |     0     |  1.97583059378e-09  |
| {'expectations.': 1, 'refu... |     0     |  1.20140501932e-09  |
| {'all': 1, 'just': 1, "don... |     0     |   2.2223349422e-10  |
+-------------------------------+-----------+---------------------+
[10 rows x 6 columns]

##Most positive reviews for the giraffe

In [43]:
giraffe_reviews[0]['review']

"Sophie, oh Sophie, your time has come. My granddaughter, Violet is 5 months old and starting to teeth. What joy little Sophie brings to Violet. Sophie is made of a very pliable rubber that is sturdy but not tough. It is quite easy for Violet to twist Sophie into unheard of positions to get Sophie into her mouth. The little nose and hooves fit perfectly into small mouths, and the drooling has purpose. The paint on Sophie is food quality.Sophie was born in 1961 in France. The maker had wondered why there was nothing available for babies and made Sophie from the finest rubber, phthalate-free on St Sophie's Day, thus the name was born. Since that time millions of Sophie's populate the world. She is soft and for babies little hands easy to grasp. Violet especially loves the bumpy head and horns of Sophie. Sophie has a long neck that easy to grasp and twist. She has lovely, sizable spots that attract Violet's attention. Sophie has happy little squeaks that bring squeals of delight from Viol

In [25]:
giraffe_reviews[1]['review']

"I'm not sure why Sophie is such a hit with the little ones, but my 7 month old baby girl is one of her adoring fans.  The rubber is softer and more pleasant to handle, and my daughter has enjoyed chewing on her legs and the nubs on her head even before she started teething.  She also loves the squeak that Sophie makes when you squeeze her.  Not sure what it is but if Sophie is amongst a pile of her other toys, my daughter will more often than not reach for Sophie.  And I have the peace of mind of knowing that only edible and safe paints and materials have been used to make Sophie, as opposed to Bright Starts and other baby toys made in China.  Now that the research is out on phthalates and other toxic substances in baby toys, I think it's more important than ever to find good quality toys that are also safe for our babies to handle and put in their mouths.  Sophie is a must-have for every new mom in my opinion.  Even if your kid is one of the few that can take or leave her, it's worth

##Show most negative reviews for giraffe

In [26]:
giraffe_reviews[-1]['review']

"My son (now 2.5) LOVED his Sophie, and I bought one for every baby shower I've gone to. Now, my daughter (6 months) just today nearly choked on it and I will never give it to her again. Had I not been within hearing range it could have been fatal. The strange sound she was making caught my attention and when I went to her and found the front curved leg shoved well down her throat and her face a purply/blue I panicked. I pulled it out and she vomited all over the carpet before screaming her head off. I can't believe how my opinion of this toy has changed from a must-have to a must-not-use. Please don't disregard any of the choking hazard comments, they are not over exaggerated!"

In [27]:
giraffe_reviews[-2]['review']

"This children's toy is nostalgic and very cute. However, there is a distinct rubber smell and a very odd taste, yes I tried it, that my baby did not enjoy. Also, if it is soiled it is extremely difficult to clean as the rubber is a kind of porus material and does not clean well. The final thing is the squeaking device inside which stopped working after the first couple of days. I returned this item feeling I had overpaid for a toy that was defective and did not meet my expectations. Please do not be swayed by the cute packaging and hype surounding it as I was. One more thing, I was given a full refund from Amazon without any problem."

In [45]:
giraffe_reviews[-3]['review']

'I wanted to love this product and was excited to buy it when I became pregnant but am now hesitant to let my baby use it after reading about the recall in Europe. Apparently, as I understand it, their toxin standards of measurement are lower than ours so they have not been recalled here (apparently we are OK with low levels of nitrates in the toys our children put in their mouths, but Europeans are not...hmmm)...Be that as it may, toxins registering even CLOSE to a dangerous level made me nervous about using. After digging around online I did discover that the company claims to have changed the product after a certain date and lists manufacturing codes so you can check yours (those listed were made after a certain date and are said to be safer). Sadly mine was not made after the &#34;improved&#34; date but I could not return it because there was no formal recall in our country. I considered returning it and hunting for one with an approved manufacturing date but man that was just too 

In [46]:
len(products)

166752

In [47]:
products.show()

In [48]:
selected_words = ['awesome', 'great', 'fantastic', 'amazing', 'love', 'horrible', 'bad', 'terrible', 'awful', 'wow', 'hate']

In [73]:
def word_count_in_dict(word_count, word):
    if word in word_count:
        return word_count[word]
    else:
        return 0
for word in selected_words:
    products[word] = products['word_count'].apply(lambda x : word_count_in_dict(x, word))

In [74]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+---------+-------+-----------+---------+
|           word_count          | sentiment | awesome | great | fantastic | amazing |
+-------------------------------+-----------+---------+-------+-----------+---------+
| {'and': 3, 'love': 1, 'it'... |     1     |    0    |   0   |     0     |    0    |
| {'and': 2, 'quilt': 1, 'it... |     1     |    0    |   0   |     0     |    0    |
| {'ingenious': 1, 'and': 3,... |     1     |    0    |   0   |     0     |    0    |
| {'and': 2, 'parents!!': 1,... |     1     |    0    |   1   |     0     |    0    |
| {'and': 2, 'this': 2, 'her... |     1     |    0    |   1   |     0     |    0    |
| {'shop': 1, 'noble': 1, 'i... |     1     |    0    |   0   |     0     |    0    |
| {'and': 2, 'all': 1, 'righ... |     1     |    0    |   0   |     0     |    0    |
| {'and': 1, 'help': 1, 'giv... |     1     |    0    |   0   |     0     |    0    |
| {'journal.': 1, 'nanny': 1... |     1     |    0    |   0   |     0     |    0    |
| {'all': 1, 'forget': 1, 'j... |     1     |    0    |   0   |     0     |    0    |
+-------------------------------+-----------+---------+-------+-----------+---------+
+------+----------+-----+----------+-------+-----+------+
| love | horrible | bad | terrible | awful | wow | hate |
+------+----------+-----+----------+-------+-----+------+
|  1   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |
+------+----------+-----+----------+-------+-----+------+
[10 rows x 16 columns]

In [59]:
def awesome_count(word_count):
    if 'great' in word_count:
        return word_count['awesom']
    else:
        return 0
products['awesome'] = products['word_count'].apply(awesome_count)

In [77]:
for word in selected_words:
    print "Number of times this " + word + " is being used: " + str(products[word].sum())

Number of times this awesome is being used: 2002
Number of times this great is being used: 42420
Number of times this fantastic is being used: 873
Number of times this amazing is being used: 1305
Number of times this love is being used: 40277
Number of times this horrible is being used: 659
Number of times this bad is being used: 3197
Number of times this terrible is being used: 673
Number of times this awful is being used: 345
Number of times this wow is being used: 131
Number of times this hate is being used: 1057


In [80]:
for word in selected_words:
    print word
    products[word].show(view='Categorical')

awesome


great


fantastic


amazing


love


...

bad


terrible


awful


wow


hate


In [81]:
train_data,test_data = products.random_split(.8, seed=0)

In [82]:
selected_words_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                                     features=selected_words,
                                                     validation_set=test_data)

Logistic regression:

--------------------------------------------------------

Number of examples          : 133448

Number of classes           : 2

Number of feature columns   : 11

...

| 4         | 5        | 1.149984     | 0.844269          | 0.843142            |

| 5         | 6        | 1.400071     | 0.844269          | 0.843142            |

| 6         | 7        | 1.648796     | 0.844269          | 0.843142            |

+-----------+----------+--------------+-------------------+---------------------+

SUCCESS: Optimal solution found.

In [83]:
selected_words_model['coefficients']

Columns:
	name	str
	index	str
	class	int
	value	float
	stderr	float

Rows: 12

Data:
+-------------+-------+-------+-----------------+------------------+
|     name    | index | class |      value      |      stderr      |
+-------------+-------+-------+-----------------+------------------+
| (intercept) |  None |   1   |  1.36728315229  | 0.00861805467825 |
|   awesome   |  None |   1   |  1.05800888878  |  0.110865296265  |
|    great    |  None |   1   |  0.883937894898 | 0.0217379527921  |
|  fantastic  |  None |   1   |  0.891303090304 |  0.154532343591  |
|   amazing   |  None |   1   |  0.892802422508 |  0.127989503231  |
|     love    |  None |   1   |  1.39989834302  | 0.0287147460124  |
|   horrible  |  None |   1   |  -1.99651800559 | 0.0973584169028  |
|     bad     |  None |   1   | -0.985827369929 | 0.0433603009142  |
|   terrible  |  None |   1   |  -2.09049998487 | 0.0967241912229  |
|    awful    |  None |   1   |  -1.76469955631 |  0.134679803365  |
+-------------+-------+-------+-----------------+------------------+
[12 rows x 5 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [117]:
selected_words_model['coefficients'].sort('value', ascending=True).head()
#selected_words_model['coefficients'].sort('value').tail()

Columns:
	name	str
	index	str
	class	int
	value	float
	stderr	float

Rows: 10

Data:
+-----------+-------+-------+------------------+-----------------+
|    name   | index | class |      value       |      stderr     |
+-----------+-------+-------+------------------+-----------------+
|  terrible |  None |   1   |  -2.09049998487  | 0.0967241912229 |
|  horrible |  None |   1   |  -1.99651800559  | 0.0973584169028 |
|   awful   |  None |   1   |  -1.76469955631  |  0.134679803365 |
|    hate   |  None |   1   |  -1.40916406276  | 0.0771983993506 |
|    bad    |  None |   1   | -0.985827369929  | 0.0433603009142 |
|    wow    |  None |   1   | -0.0541450123332 |  0.275616449416 |
|   great   |  None |   1   |  0.883937894898  | 0.0217379527921 |
| fantastic |  None |   1   |  0.891303090304  |  0.154532343591 |
|  amazing  |  None |   1   |  0.892802422508  |  0.127989503231 |
|  awesome  |  None |   1   |  1.05800888878   |  0.110865296265 |
+-----------+-------+-------+------------------+-----------------+
[10 rows x 5 columns]

In [86]:
selected_words_model.evaluate(test_data,metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 100001
 
 Data:
 +-----------+-----+-----+-------+------+
 | threshold | fpr | tpr |   p   |  n   |
 +-----------+-----+-----+-------+------+
 |    0.0    | 1.0 | 1.0 | 27976 | 5328 |
 |   1e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   2e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   3e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   4e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   5e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   6e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   7e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   8e-05   | 1.0 | 1.0 | 27976 | 5328 |
 |   9e-05   | 1.0 | 1.0 | 27976 | 5328 |
 +-----------+-----+-----+-------+------+
 [100001 rows x 5 columns]
 Note: Only the head of the SFrame is printed.
 You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.}

In [109]:
selected_words_model.show(view='Evaluation')

In [92]:
diaper_champ_reviews = products[products['name'] == "Baby Trend Diaper Champ"]

In [93]:
diaper_champ_reviews['predicted_sentiment'] = selected_words_model.predict(diaper_champ_reviews, output_type='probability')

In [97]:
diaper_champ_reviews = diaper_champ_reviews.sort('predicted_sentiment', ascending=False)
diaper_champ_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------+-------------------------------+--------+
|           name          |             review            | rating |
+-------------------------+-------------------------------+--------+
| Baby Trend Diaper Champ | I LOVE LOVE LOVE this prod... |  4.0   |
| Baby Trend Diaper Champ | Love it, love it, love it!... |  5.0   |
| Baby Trend Diaper Champ | I received my Diaper Champ... |  5.0   |
| Baby Trend Diaper Champ | Works great - no smells.  ... |  5.0   |
| Baby Trend Diaper Champ | I love this diaper pale an... |  5.0   |
| Baby Trend Diaper Champ | I've worked with kids more... |  5.0   |
| Baby Trend Diaper Champ | Love the Diaper Champ.  I ... |  4.0   |
| Baby Trend Diaper Champ | I love this diaper pail!  ... |  5.0   |
| Baby Trend Diaper Champ | I have a 10 year old daugh... |  5.0   |
| Baby Trend Diaper Champ | We had 2 diaper Genie's bo... |  4.0   |
+-------------------------+-------------------------------+--------+
+-------------------------------+-----------+---------+-------+-----------+---------+
|           word_count          | sentiment | awesome | great | fantastic | amazing |
+-------------------------------+-----------+---------+-------+-----------+---------+
| {'rating': 1, 'contacted':... |     1     |    0    |   1   |     0     |    0    |
| {'instead': 1, 'all': 1, '... |     1     |    0    |   0   |     0     |    0    |
| {'bags.': 1, "don't": 1, '... |     1     |    0    |   0   |     0     |    0    |
| {'and': 2, 'bags.': 1, 'ga... |     1     |    0    |   2   |     0     |    0    |
| {'and': 3, 'love': 1, 'use... |     1     |    0    |   2   |     0     |    0    |
| {'and': 4, 'genies': 1, 'a... |     1     |    0    |   0   |     0     |    0    |
| {'reviews,': 1, 'infant': ... |     1     |    0    |   0   |     0     |    0    |
| {'and': 3, 'love': 2, 'bei... |     1     |    0    |   0   |     0     |    0    |
| {'lysol': 1, 'all': 1, 'ju... |     1     |    0    |   0   |     0     |    0    |
| {'hand.': 1, 'both': 1, '(... |     1     |    0    |   0   |     0     |    0    |
+-------------------------------+-----------+---------+-------+-----------+---------+
+------+----------+-----+----------+-------+-----+------+---------------------+
| love | horrible | bad | terrible | awful | wow | hate | predicted_sentiment |
+------+----------+-----+----------+-------+-----+------+---------------------+
|  3   |    0     |  0  |    0     |   0   |  0  |  0   |    0.998423414594   |
|  3   |    0     |  0  |    0     |   0   |  0  |  0   |    0.996192539732   |
|  3   |    0     |  0  |    0     |   0   |  0  |  0   |    0.996192539732   |
|  1   |    0     |  0  |    0     |   0   |  0  |  0   |    0.989387539605   |
|  1   |    0     |  0  |    0     |   0   |  0  |  0   |    0.989387539605   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
+------+----------+-----+----------+-------+-----+------+---------------------+
[10 rows x 17 columns]

In [111]:
#print selected_words_model.predict(products[products['love'] > 30], output_type='probability')
print sentiment_model.predict(diaper_champ_reviews[0:1], output_type='probability')



[0.9999936520356157]


In [110]:
test_data['rating'].show(view = 'Categorical')

In [118]:
diaper_champ_reviews['predicted_sentiment_model'] = sentiment_model.predict(diaper_champ_reviews, output_type='probability')

In [119]:
diaper_champ_reviews = diaper_champ_reviews.sort('predicted_sentiment_model', ascending=False)
diaper_champ_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int
	predicted_sentiment	float
	predicted_sentiment_model	float

Rows: 10

Data:
+-------------------------+-------------------------------+--------+
|           name          |             review            | rating |
+-------------------------+-------------------------------+--------+
| Baby Trend Diaper Champ | Baby Luke can turn a clean... |  5.0   |
| Baby Trend Diaper Champ | I LOOOVE this diaper pail!... |  5.0   |
| Baby Trend Diaper Champ | We researched all of the d... |  4.0   |
| Baby Trend Diaper Champ | My baby is now 8 months an... |  5.0   |
| Baby Trend Diaper Champ | This is absolutely, by far... |  5.0   |
| Baby Trend Diaper Champ | Diaper Champ or Diaper Gen... |  5.0   |
| Baby Trend Diaper Champ | Wow!  This is fabulous.  I... |  5.0   |
| Baby Trend Diaper Champ | I originally put this item... |  5.0   |
| Baby Trend Diaper Champ | Two girlfriends and two fa... |  5.0   |
| Baby Trend Diaper Champ | I am one of those super-cr... |  5.0   |
+-------------------------+-------------------------------+--------+
+-------------------------------+-----------+---------+-------+-----------+---------+
|           word_count          | sentiment | awesome | great | fantastic | amazing |
+-------------------------------+-----------+---------+-------+-----------+---------+
| {'all': 1, 'less': 1, "fri... |     1     |    0    |   0   |     0     |    0    |
| {'just': 1, 'over': 1, 'rw... |     1     |    0    |   0   |     0     |    0    |
| {'all': 2, 'just': 4, "don... |     1     |    0    |   0   |     0     |    0    |
| {"don't": 1, 'able': 2, 'o... |     1     |    0    |   2   |     0     |    0    |
| {'just': 3, 'money': 1, 's... |     1     |    0    |   0   |     0     |    0    |
| {'son': 2, 'all': 1, 'bags... |     1     |    0    |   0   |     0     |    0    |
| {'and': 4, 'this': 3, 'sti... |     1     |    0    |   0   |     0     |    0    |
| {'lysol': 1, 'all': 2, 'ba... |     1     |    0    |   0   |     0     |    0    |
| {'just': 1, '-': 3, 'both'... |     1     |    0    |   0   |     0     |    0    |
| {'all': 1, 'humid': 1, 'ju... |     1     |    0    |   0   |     0     |    0    |
+-------------------------------+-----------+---------+-------+-----------+---------+
+------+----------+-----+----------+-------+-----+------+---------------------+
| love | horrible | bad | terrible | awful | wow | hate | predicted_sentiment |
+------+----------+-----+----------+-------+-----+------+---------------------+
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |    0.796940851291   |
|  1   |    0     |  0  |    0     |   0   |  0  |  0   |    0.940876393428   |
|  0   |    0     |  1  |    0     |   0   |  0  |  0   |     0.5942241719    |
|  0   |    0     |  1  |    0     |   0   |  0  |  0   |    0.895606298305   |
|  2   |    0     |  0  |    0     |   0   |  0  |  0   |    0.984739056527   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |    0.796940851291   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |    0.796940851291   |
|  0   |    0     |  0  |    0     |   0   |  0  |  0   |    0.796940851291   |
|  0   |    1     |  0  |    0     |   0   |  0  |  0   |    0.347684052736   |
|  1   |    0     |  0  |    0     |   0   |  0  |  0   |    0.940876393428   |
+------+----------+-----+----------+-------+-----+------+---------------------+
+---------------------------+
| predicted_sentiment_model |
+---------------------------+
|       0.999999937267      |
|       0.999999917406      |
|       0.999999899509      |
|       0.999999836182      |
|       0.999999824745      |
|       0.999999759315      |
|       0.999999692111      |
|       0.999999642488      |
|       0.999999604504      |
|       0.999999486804      |
+---------------------------+
[10 row

In [121]:
print selected_words_model.predict(diaper_champ_reviews[0:1], output_type='probability')

[0.7969408512906704]
